In [93]:
from google.cloud import bigquery
 

In [2]:
from google.cloud import storage

In [3]:
storage_client = storage.Client(project = 'event-trigger-cloud-storage')

In [4]:
list(storage_client.list_buckets())

[<Bucket: bucket-gcs-to-bq-archival-d>,
 <Bucket: bucket-gcs-to-bq-d>,
 <Bucket: cf-gcs-to-bq-d>,
 <Bucket: event-trigger-cloud-storage-d>,
 <Bucket: gcf-v2-sources-617230007681-asia-south1>]

In [5]:
from google.cloud import logging

In [6]:
from datetime import datetime, timedelta, timezone

In [7]:
log_client  = logging.Client()
now         = datetime.now(timezone.utc)
yesterday   = now - timedelta(days = 3)
yesterday   = yesterday.date()
filter_     = f'timestamp >= "{yesterday}T00:00:00Z" AND resource.type = "cloud_function" severity = "INFO"'

In [8]:
log_entries = log_client.list_entries(filter_ = filter_ , order_by = logging.DESCENDING, max_results = 1)

In [9]:
entry = list(log_entries)[0]

In [16]:
entry.payload

OrderedDict([('@type', 'type.googleapis.com/google.cloud.audit.AuditLog'),
             ('authenticationInfo', {'principalEmail': 'ranram927@gmail.com'}),
             ('requestMetadata',
              {'requestAttributes': {'time': '2024-08-03T11:29:32.915922Z',
                'auth': {}},
               'destinationAttributes': {}}),
             ('serviceName', 'cloudfunctions.googleapis.com'),
             ('methodName',
              'google.cloud.functions.v1.CloudFunctionsService.GenerateUploadUrl'),
             ('authorizationInfo',
              [{'resource': 'projects/event-trigger-cloud-storage/locations/us-central1',
                'permission': 'cloudfunctions.functions.sourceCodeSet',
                'granted': True,
                'resourceAttributes': {}}]),
             ('resourceName',
              'projects/event-trigger-cloud-storage/locations/us-central1'),
             ('resourceLocation', {'currentLocations': ['us-central1']})])

In [17]:
bucket = storage_client.get_bucket('cf-gcs-to-bq-d')

In [20]:
blob = bucket.blob('cf_logs.txt')

In [22]:
blob.upload_from_string(str(entry))

In [ ]:
def get_logs_from_function(bucket_name, storage_client):

    log_client  = logging.Client()
    today       = datetime.now(timezone.utc).date()
    filter_     = f'timestamp >= "{today}T00:00:00Z" AND resource.type = "cloud_function"'
    log_entries = log_client.list_entries(filter_ = filter_ , order_by = logging.DESCENDING)
    latest_log  = None
    for entry in log_entries:
        latest_log = entry
        break 
    if latest_log:
        print(f"Latest Log FROM cloud_function: {latest_log}")
        

In [97]:
from pandas_gbq import read_gbq,to_gbq

In [98]:
bq_client = bigquery.Client(project = 'event-trigger-cloud-storage')

In [99]:
table_ref = bq_client.dataset('orders_stg_dataset').table('orders_stg_table')

In [100]:
query_results = bq_client.query(f""" SELECT order_id,
                    order_customer_id,
                    order_date,
                    order_status
                  FROM
                  `{bq_client.project}.orders_stg_dataset.orders_stg_table`
            """)

In [101]:
df = read_gbq(f'{bq_client.project}.orders_stg_dataset.orders_stg_table')

c:\Users\Divya\AppData\Local\Programs\Python\Python310\lib\site-packages\google\cloud\bigquery\table.py:2379: UserWarning: A progress bar was requested, but there was an error loading the tqdm library. Please install tqdm to use the progress bar functionality.
  record_batch = self.to_arrow(


In [129]:
query = f""" SELECT order_id,
                    order_customer_id,
                    order_date,
                    order_status,
                    source_timestamp
                  FROM
                  `{bq_client.project}.orders_stg_dataset.orders_stg_table`
            """

In [130]:
stage_table_df = read_gbq(query)

c:\Users\Divya\AppData\Local\Programs\Python\Python310\lib\site-packages\google\cloud\bigquery\table.py:2379: UserWarning: A progress bar was requested, but there was an error loading the tqdm library. Please install tqdm to use the progress bar functionality.
  record_batch = self.to_arrow(


In [131]:
stage_table_df.dtypes

order_id                           Int64
order_customer_id                  Int64
order_date           datetime64[us, UTC]
order_status                      object
source_timestamp     datetime64[us, UTC]
dtype: object

In [105]:
stage_table_df.dtypes 

order_id                           Int64
order_customer_id                  Int64
order_date           datetime64[us, UTC]
order_status                      object
dtype: object

In [106]:
with open(r"C:\Users\Divya\JSON_NEWLINE_DELIMITED_DATA\orders_03_08_2024_14_09", 'r') as file:
    print(file.read())

{"order_id":1,"order_date":"2013-07-25 00:00:00.0","order_customer_id":11599,"order_status":"CLOSED"}
{"order_id":2,"order_date":"2013-07-25 00:00:00.0","order_customer_id":256,"order_status":"PAYMENT_REVIEW"}
{"order_id":3,"order_date":"2013-07-25 00:00:00.0","order_customer_id":12111,"order_status":"COMPLETE"}
{"order_id":4,"order_date":"2013-07-25 00:00:00.0","order_customer_id":8827,"order_status":"CLOSED"}
{"order_id":5,"order_date":"2013-07-25 00:00:00.0","order_customer_id":11318,"order_status":"COMPLETE"}
{"order_id":6,"order_date":"2013-07-25 00:00:00.0","order_customer_id":7130,"order_status":"COMPLETE"}
{"order_id":7,"order_date":"2013-07-25 00:00:00.0","order_customer_id":4530,"order_status":"COMPLETE"}
{"order_id":8,"order_date":"2013-07-25 00:00:00.0","order_customer_id":2911,"order_status":"PROCESSING"}
{"order_id":9,"order_date":"2013-07-25 00:00:00.0","order_customer_id":5657,"order_status":"COMPLETE"}
{"order_id":10,"order_date":"2013-07-25 00:00:00.0","order_customer

In [107]:
import pandas as pd

In [108]:
source_df = pd.read_json(r"C:\Users\Divya\JSON_NEWLINE_DELIMITED_DATA\orders_03_08_2024_14_09", lines = True)

In [109]:
source_df = source_df[['order_id', 'order_customer_id', 'order_date', 'order_status']]

In [110]:
source_df['order_date'] = pd.to_datetime(source_df['order_date']).dt.tz_localize('UTC')

In [111]:
source_df['order_date'] = pd.to_datetime(source_df['order_date']).dt.strftime('%Y-%m-%d %H:%M:%S%z')

In [112]:
source_df   

order_id  order_customer_id                order_date     order_status
0             1              11599  2013-07-25 00:00:00+0000           CLOSED
1             2                256  2013-07-25 00:00:00+0000   PAYMENT_REVIEW
2             3              12111  2013-07-25 00:00:00+0000         COMPLETE
3             4               8827  2013-07-25 00:00:00+0000           CLOSED
4             5              11318  2013-07-25 00:00:00+0000         COMPLETE
...         ...                ...                       ...              ...
68878     68879                778  2014-07-09 00:00:00+0000         COMPLETE
68879     68880               1117  2014-07-13 00:00:00+0000         COMPLETE
68880     68881               2518  2014-07-19 00:00:00+0000  PENDING_PAYMENT
68881     68882              10000  2014-07-22 00:00:00+0000          ON_HOLD
68882     68883               5533  2014-07-23 00:00:00+0000         COMPLETE

[68883 rows x 4 columns]

In [113]:
source_df.dtypes

order_id              int64
order_customer_id     int64
order_date           object
order_status         object
dtype: object

In [132]:
source_stg_df = pd.concat([source_df, stage_table_df], ignore_index = True)

In [115]:
len(source_stg_df)

137766

In [124]:
source_stg_df['order_date'] = pd.to_datetime(source_stg_df['order_date'], format='%Y-%m-%d %H:%M:%S%z')

# Format datetime objects to the desired string format with +00:00
source_stg_df['order_date'] = source_stg_df['order_date'].apply(lambda x: x.strftime('%Y-%m-%d %H:%M:%S%z')[:19] + ':' + x.strftime('%z')[3:])

C:\Users\Divya\AppData\Local\Temp\ipykernel_48552\1190205294.py:1: FutureWarning: In a future version of pandas, parsing datetimes with mixed time zones will raise an error unless `utc=True`. Please specify `utc=True` to opt in to the new behaviour and silence this warning. To create a `Series` with mixed offsets and `object` dtype, please use `apply` and `datetime.datetime.strptime`
  source_stg_df['order_date'] = pd.to_datetime(source_stg_df['order_date'], format='%Y-%m-%d %H:%M:%S%z')


In [133]:
source_stg_df

order_id  order_customer_id                 order_date  \
0              1              11599   2013-07-25 00:00:00+0000   
1              2                256   2013-07-25 00:00:00+0000   
2              3              12111   2013-07-25 00:00:00+0000   
3              4               8827   2013-07-25 00:00:00+0000   
4              5              11318   2013-07-25 00:00:00+0000   
...          ...                ...                        ...   
137761     45034               8651  2014-04-29 00:00:00+00:00   
137762     11342               5780  2013-10-03 00:00:00+00:00   
137763     11331              11637  2013-10-03 00:00:00+00:00   
137764     11405               2263  2013-10-03 00:00:00+00:00   
137765     25608              10838  2013-12-30 00:00:00+00:00   

           order_status                 source_timestamp  
0                CLOSED                              NaT  
1        PAYMENT_REVIEW                              NaT  
2              COMPLETE                              NaT  
3                CLOSED                              NaT  
4              COMPLETE                              NaT  
...                 ...                              ...  
137761  SUSPECTED_FRAUD 2024-08-05 05:01:05.931746+00:00  
137762  SUSPECTED_FRAUD 2024-08-05 05:01:05.931746+00:00  
137763  SUSPECTED_FRAUD 2024-08-05 05:01:05.931746+00:00  
137764  SUSPECTED_FRAUD 2024-08-05 05:01:05.931746+00:00  
137765  SUSPECTED_FRAUD 2024-08-05 05:01:05.931746+00:00  

[137766 rows x 5 columns]

In [122]:
source_stg_df['order_date'].unique

<bound method Series.unique of 0          2013-07-25 00:00:00+0000
1          2013-07-25 00:00:00+0000
2          2013-07-25 00:00:00+0000
3          2013-07-25 00:00:00+0000
4          2013-07-25 00:00:00+0000
                    ...            
137761    2014-04-29 00:00:00+00:00
137762    2013-10-03 00:00:00+00:00
137763    2013-10-03 00:00:00+00:00
137764    2013-10-03 00:00:00+00:00
137765    2013-12-30 00:00:00+00:00
Name: order_date, Length: 137766, dtype: object>

In [126]:
source_stg_df.dtypes 

order_id              Int64
order_customer_id     Int64
order_date           object
order_status         object
dtype: object

In [138]:
source_stg_df = source_stg_df.drop_duplicates(ignore_index = True)

In [139]:
source_stg_df

order_id  order_customer_id                 order_date  \
0              1              11599   2013-07-25 00:00:00+0000   
1              2                256   2013-07-25 00:00:00+0000   
2              3              12111   2013-07-25 00:00:00+0000   
3              4               8827   2013-07-25 00:00:00+0000   
4              5              11318   2013-07-25 00:00:00+0000   
...          ...                ...                        ...   
137761     45034               8651  2014-04-29 00:00:00+00:00   
137762     11342               5780  2013-10-03 00:00:00+00:00   
137763     11331              11637  2013-10-03 00:00:00+00:00   
137764     11405               2263  2013-10-03 00:00:00+00:00   
137765     25608              10838  2013-12-30 00:00:00+00:00   

           order_status  
0                CLOSED  
1        PAYMENT_REVIEW  
2              COMPLETE  
3                CLOSED  
4              COMPLETE  
...                 ...  
137761  SUSPECTED_FRAUD  
137762  SUSPECTED_FRAUD  
137763  SUSPECTED_FRAUD  
137764  SUSPECTED_FRAUD  
137765  SUSPECTED_FRAUD  

[137766 rows x 4 columns]

In [119]:
len(source_stg_df)

137766

In [120]:
full_table_id = f'event-trigger-cloud-storage.

SyntaxError: unterminated string literal (detected at line 1) (1345392185.py, line 1)

In [ ]:
read_gbq()